In [1]:
import nltk
import spacy
import re
import unidecode
from nltk.corpus import stopwords
from numpy import *
import pandas as pd 
import requests 
import re
import pdfplumber
from gensim.models import Word2Vec
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np


In [2]:
# Download Greek stopwords
nltk.download('stopwords')
greek_stopwords = set(stopwords.words('greek'))

# Load Greek NLP model
#!python -m spacy download el_core_news_sm
nlp = spacy.load('el_core_news_sm')  # Greek NLP model


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\steve\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
def preprocess_text(text):
    #process our text and return it as embeddings
    # Remove punctuation and numbers (keeping Greek characters)
    text = re.sub(r"[^α-ωΑ-Ωάέήίόύώϊϋΐΰ\s]", "", text)

    # Convert to lowercase
    text = text.lower()

    # Split text into sentences
    sentences = text.split('\n')  # You can also use sentence segmentation via spaCy if needed
    
    # Initialize an empty list to hold the tokenized sentences
    tokenized_sentences = []

    # Tokenize each sentence
    for sentence in sentences:
        # Tokenize using spaCy
        doc = nlp(sentence)
        
        # Extract tokens (words) and filter out stopwords and punctuation
        tokens = [token.lemma_ for token in doc if token.text not in greek_stopwords and not token.is_punct]
        
        # Filter out short tokens (length > 2)
        tokens = [token for token in tokens if len(token) > 2]

        # Add the tokens of the sentence to the list of sentences
        if tokens:
            tokenized_sentences.append(tokens)

    return tokenized_sentences


Let us create a list of books , upon which we will train our model.

In [4]:
books = ['https://1oholargou.wordpress.com/wp-content/uploads/2012/08/13078091-31328.pdf',
        'https://derkamerad.com/wp-content/uploads/2016/09/cebcceb1cf84cf89cebcceb5cebdceb1-cf87cf89cebcceb1cf84ceb1-ceb4ceb9ceb4cf89-cf83cf89cf84ceb7cf81ceb9cebfcf85.pdf',
          'https://schoolpress.sch.gr/periodista/files/2022/02/%CE%A4%CE%BF-%CE%9C%CE%BF%CE%BD%CF%8C%CE%B3%CF%81%CE%B1%CE%BC%CE%BC%CE%B11.pdf',
          'http://7gym-athin.att.sch.gr/wordpress/wp-content/uploads/2020/03/Aiolike-Ge-Elias-Benezes.pdf',
          'https://books.shopflix.gr/9786180103106.pdf',
          'https://www.patakis.gr/files/1187291.pdf',
          'https://manifestolibrary.noblogs.org/files/2020/10/441339144-%CE%86%CF%81%CE%B7%CF%82-%CE%91%CE%BB%CE%B5%CE%BE%CE%AC%CE%BD%CE%B4%CF%81%CE%BF%CF%85-%CF%84%CE%BF-%CE%BA%CE%B9%CE%B2%CF%8E%CF%84%CE%B9%CE%BF-pdf.pdf', #sometimes this one crushes
         #'https://www.xn--ixauk7au.gr/%CE%B4%CF%89%CF%81%CE%B5%CE%AC%CE%BD-ebooks/Alexandros_Papadiamandis-I_Fonissa.pdf' #doesnt work
         'https://esperos-library.ucoz.com/_ld/1/177_psathas.pdf',
         'https://archeia.moec.gov.cy/sm/371/diig_vizyinou_odig_ekpaid.pdf' #this works
         #'https://blogs.sch.gr/idaragiannis/files/2017/02/ena-paidi-metraei-t-astra.pdf' #doesnt work
 ]

In [5]:
def download_book(book, i):
    
    #download the book and save it as a pdf file
    response = requests.get(book)
    pdf_path = f"{i}.pdf"
    with open(pdf_path, "wb") as f:
        f.write(response.content)
        
    #save the pdf as a string
    with pdfplumber.open(pdf_path) as pdf:
        text = ""
        for page in pdf.pages:
            text += page.extract_text() + "\n"  
    return text

Download our books, save them as pdfs, convert them to strings, tokenize them, and add them to our corpus.

In [6]:
all_tokens = []
corpus = []
for i,book in enumerate(books):
    book_text = download_book(book, i)
    tokens = preprocess_text(book_text)
    book_text_processed = " ".join(word for sentence in tokens for word in sentence)
    corpus.append(book_text_processed)
    all_tokens.extend(tokens)

In [7]:
print(all_tokens)

[['ηλιο', 'βενεζη'], ['ακαδημία', 'αθηνών'], ['νούμερο'], ['βιβλιο', 'σκλαβια'], ['εισαγωγή', 'δημήτρης', 'δασκαλόπουλος'], ['τεσσαρακοστος', 'εβδομος', 'εκδοση'], ['βιβλιοπωλειον', 'εστια'], ['κολλαρο', 'σιος'], ['αθηνα'], ['νούμερο', 'είμαι', 'ίδιος', 'ταυτότητα', 'συγγραφέα', 'παιδί'], ['δεκαοκτώς', 'χρόνος', 'οδηγώ', 'από', 'τούρκους', 'σε ο', 'κάτεργα', 'ανατολή'], ['βιβλίο', 'είμαι', 'ένας', 'συγκλονιστικός', 'χρονικός', 'γραμμένος', 'αίμα', 'όπως', 'επισημαίνω'], ['βενέζης', 'προσθέτοντα', 'λέω', 'καυτής', 'ύλη', 'σάρκα', 'στάζω'], ['αίμα', 'μου', 'πλημμυρίζω', 'σελίδα', 'αρχικός', 'μορφή', 'γράφτηκε'], ['ξαναδουλεύτηκε', 'οπότε', 'εκδόθηκε', 'πρώτος', 'φορά', 'επιτυχία'], ['σημείωσε', 'είμαι', 'τεράστιος', 'ακόμα', 'έξω', 'από', 'ελληνικός', 'χώρος'], ['ηλία', 'βενέζης', 'βιβλίομαρτυρία', 'είμαι', 'γραώνμ', 'πρώτος', 'πρόσωπος'], ['πραγματικός', 'όνομα', 'αφηγητήσυγγραφέα', 'γεννήθηκε', 'αϊβαλί', 'ρθε'], ['Ελλάδα', 'μικρασιατικός', 'καταστροφή', 'θεωρώ', 'ένας', 'από'], ['κυριό

In [8]:
print(corpus)

['ηλιο βενεζη ακαδημία αθηνών νούμερο βιβλιο σκλαβια εισαγωγή δημήτρης δασκαλόπουλος τεσσαρακοστος εβδομος εκδοση βιβλιοπωλειον εστια κολλαρο σιος αθηνα νούμερο είμαι ίδιος ταυτότητα συγγραφέα παιδί δεκαοκτώς χρόνος οδηγώ από τούρκους σε ο κάτεργα ανατολή βιβλίο είμαι ένας συγκλονιστικός χρονικός γραμμένος αίμα όπως επισημαίνω βενέζης προσθέτοντα λέω καυτής ύλη σάρκα στάζω αίμα μου πλημμυρίζω σελίδα αρχικός μορφή γράφτηκε ξαναδουλεύτηκε οπότε εκδόθηκε πρώτος φορά επιτυχία σημείωσε είμαι τεράστιος ακόμα έξω από ελληνικός χώρος ηλία βενέζης βιβλίομαρτυρία είμαι γραώνμ πρώτος πρόσωπος πραγματικός όνομα αφηγητήσυγγραφέα γεννήθηκε αϊβαλί ρθε Ελλάδα μικρασιατικός καταστροφή θεωρώ ένας από κυριότερους εκπροσώπους γενιά νεοελληνικός πεζογραφία τεσσαρακοστή τρίτος έκδοση βιβλίου ηλία βενέζη νούμερο αναστοιχειοθετήθηκε προτάχθηκε αυτός εισαγωγικός κείμενο δημήτρη δασκαλόπουλου νέος έκδοση κυκλοφόρησε φεβρουάριο σειρά νεοελληνικός λογοτεχνία      τεσσαρακοστός έβδομος έκδοση σεπτέμβριος βιβλιοπωλ

In [9]:
# response = requests.get('https://1oholargou.wordpress.com/wp-content/uploads/2012/08/13078091-31328.pdf')
# pdf_path = "downloaded.pdf"
# with open(pdf_path, "wb") as f:
#     f.write(response.content)

In [10]:

# pdf_path = "downloaded.pdf"  

# with pdfplumber.open(pdf_path) as pdf:
#     text = ""
#     for page in pdf.pages:
#         text += page.extract_text() + "\n"  

# print(text) 


In [11]:
# tokens = preprocess_text(text)
# print(tokens)


Let us train a tf idf vectorizer on these sentences!

In [12]:
vectorizer = TfidfVectorizer()
tfidf_matrix = vectorizer.fit_transform(corpus)

# Get feature names (words) and their scores
feature_names = vectorizer.get_feature_names_out()
tfidf_scores = np.array(tfidf_matrix.mean(axis=0)).flatten()

# Create a dictionary mapping words to their TF-IDF scores
word_tfidf = dict(zip(feature_names, tfidf_scores))

Check the words with the highest tf idf score, aka common words that are non distinctive!

In [13]:
# Inspect top TF-IDF scores
print("Top 100 words by TF-IDF score:")
sorted_tfidf = sorted(word_tfidf.items(), key=lambda x: x[1], reverse=True)
for word, score in sorted_tfidf[:100]:
    print(word, score)

Top 100 words by TF-IDF score:
μου 0.33014664606819943
ένας 0.2530371594097735
είμαι 0.20779332480623672
από 0.17882956683666243
εγώ 0.16465068443143457
έχω 0.1474751591969245
αυτός 0.1292789469467745
σε 0.12496732239695829
άλλος 0.08428008524747986
όλος 0.06752035464073736
ότι 0.06104674599189961
λέγω 0.050800701612828535
στός 0.050010273955539634
πού 0.044953947197309496
γιατί 0.04481225488100391
πολύ 0.04365656252343504
μεγάλος 0.04237617895128592
γιά 0.037859848875035566
σαν 0.03730300193102884
μέσα 0.035844103864142676
σου 0.03566138082470396
μπορώ 0.035509227569849304
κάνω 0.03512706315647767
αλλά 0.03451984485933954
πιο 0.03416303626139752
εκεί 0.033695583088690986
γίνομαι 0.033508399964033785
δυο 0.03350521543352992
τώρα 0.033403930492964425
οποίος 0.03337909554757737
ώρα 0.03326407292105438
όταν 0.03310431508532795
εκείνος 0.03301402822233744
λέει 0.03234874827343096
όμως 0.03223492598267508
πρώτος 0.031902623120361503
ακός 0.03143533976883117
χέρι 0.031349554303658156
ακόμα 0

Define a function that filters words, based on their tf idf score, since we do not care about words that are all over our documents, because they are not distinctive in terms of our target word!

In [14]:
tfidf_threshold = np.percentile(list(word_tfidf.values()), 90)  # Top 10% most common words

# Function to filter words based on TF-IDF scores
def filter_words_by_tfidf(similar_words, word_tfidf, threshold):
    return [(word, score) for word, score in similar_words if word_tfidf.get(word, 0) > threshold]

In [15]:
print(tokens)

[['υπουργειο', 'παιδεια', 'πολιτισμου'], ['γεώργιος', 'βιζυηνός'], ['νεοελληνικός', 'διηγήμα'], ['βιβλίο', 'εκπαιδευτικός'], ['ρευνα', 'συγγραφή'], ['μαριλένα', 'πόρακου'], ['λευκωσιος'], ['γεώργιος', 'βιζυηνός', 'νεοελληνικός', 'διηγήμα'], ['υπουργειο', 'παιδεια', 'πολιτισμου'], ['διευθυνση', 'μεση', 'εκπαιδευση'], ['γεώργιος', 'βιζυηνός', 'νεοελληνικός', 'διηγήμα'], ['βιβλίο', 'εκπαιδευτικός', 'τάξη', 'λυκείος'], ['ρευνα', 'συγγραφή'], ['μαριλένα', 'πόρακου'], ['εποπτεία', 'επιμέλεια', 'κειμένου'], ['λεωνίδαςς', 'γαλάζης', 'εμε', 'φιλολογικός', 'μαθημάτων'], ['ζωή', 'οδυσσέωςπολυδώρου', 'εμε', 'φιλολογικός', 'μαθημάτων'], ['ελένος', 'κτίστης', 'εμε', 'φιλολογικός', 'μαθημάτων'], ['επιστημονικός', 'καθοδήγηση'], ['μαρίνα', 'ροδοσθένουςμπαλάφα', 'επίκουρη', 'καθηγήτριο', 'λογοτεχνία'], ['πανεπιστήμιο', 'λευκωσία'], ['θεοδόση', 'πυλαρινός', 'ομότιμος', 'καθηγητός', 'λογοτεχνία', 'ιόνιος'], ['πανεπιστήμιο', 'ακαδημαϊκός', 'επόπτος', 'αναλυτικός', 'πρόγραμμα', 'λογοτεχνία'], ['βιβλιο', 'ε

In [16]:
for sentence in tokens:
    for word in sentence:
        if word == 'γυναίκα':
            print('True')
            

True
True
True
True
True
True
True
True
True
True


In [17]:

# Train Word2Vec Model
model = Word2Vec(all_tokens, vector_size=100, window=5, min_count=3, workers=4)

# Save model for future use
model.save("greek_word2vec.model")


In [18]:
word_index = model.wv.key_to_index.get('μαύρος', 'Word not found in vocabulary')

print(f"Index of '': {word_index}")

Index of '': 2412


In [19]:
vocab = model.wv.index_to_key  # List of words in the model's vocabulary
print(vocab[146]) 

δια


In [20]:

similar_words_woman = model.wv.most_similar('γυναίκα', topn=1000)
similar_words_man = model.wv.most_similar('άντρας', topn=1000)

Similar words to man, without tf idf

In [21]:
print("\nSimilar words to 'γυναίκα':")
for word in similar_words_woman:
    print(word)


Similar words to 'γυναίκα':
('τότης', 0.9996260404586792)
('καθώς', 0.9996076226234436)
('γράφω', 0.9995958805084229)
('όπλο', 0.9995951652526855)
('τσι', 0.9995841979980469)
('μόνος', 0.9995818138122559)
('κορίτσι', 0.999579906463623)
('γυναικόπαιδα', 0.9995772242546082)
('παππός', 0.9995735287666321)
('σχεδόν', 0.9995690584182739)
('λυσίμαχος', 0.9995675086975098)
('μάνα', 0.9995602965354919)
('αντάρτης', 0.9995598793029785)
('εαυτός', 0.9995537996292114)
('φέρω', 0.9995481371879578)
('καθένας', 0.9995463490486145)
('δείχνω', 0.9995449185371399)
('πορεία', 0.9995430111885071)
('μεταξύ', 0.999540388584137)
('αφήνω', 0.9995403289794922)
('θάνατος', 0.9995378255844116)
('πάντων', 0.9995373487472534)
('αρχή', 0.9995320439338684)
('πράγματι', 0.9995284676551819)
('αφού', 0.9995200037956238)
('κόσμος', 0.9995194673538208)
('λληνη', 0.9995164275169373)
('πάω', 0.9995151162147522)
('σύντροφος', 0.9995137453079224)
('χαρά', 0.9995068311691284)
('οπλαρχηγός', 0.9995050430297852)
('ιστορία', 0

Similar words to woman, without tf idf

In [22]:
print("\nSimilar words to 'άνδρας':")
for word in similar_words_man:
    print(word)


Similar words to 'άνδρας':
('πέντε', 0.9996445178985596)
('πέρασε', 0.9995888471603394)
('δέκα', 0.9995840191841125)
('δύο', 0.9995790123939514)
('τέσσερις', 0.9995744228363037)
('είκοσι', 0.999538242816925)
('σειρά', 0.9995317459106445)
('περίπου', 0.9995279312133789)
('στρατιώτης', 0.9995180368423462)
('κάρο', 0.9995015263557434)
('μάχη', 0.9994887709617615)
('πήρε', 0.9994856119155884)
('φτάνω', 0.9994778633117676)
('ρίχνω', 0.999472975730896)
('τόσος', 0.9994676113128662)
('ίσαμε', 0.9994609355926514)
('βάρδιος', 0.9994525909423828)
('βράδυ', 0.9994474053382874)
('κοντά', 0.9994429349899292)
('τριάντα', 0.999441921710968)
('ομάδα', 0.9994308948516846)
('ήρθε', 0.9994054436683655)
('ερχόταν', 0.9993978142738342)
('έξω', 0.9993889331817627)
('άλλον', 0.9993864893913269)
('αράδα', 0.9993820190429688)
('οικογένεια', 0.9993820190429688)
('μήνας', 0.9993804097175598)
('πλήθος', 0.9993802309036255)
('βήμα', 0.9993789196014404)
('κιόλας', 0.9993788003921509)
('σύντροφος', 0.99937844276428

In [23]:
word_at_index_656 = model.wv.index_to_key[656]
print(word_at_index_656)

αρκετά


Use tf idf for both groups, in order to filter non distinctive words (aka words that appear all over the book, and not just our target tokens)

In [24]:

similar_words_man_filtered = filter_words_by_tfidf(similar_words_man, word_tfidf, tfidf_threshold)
similar_words_woman_filtered = filter_words_by_tfidf(similar_words_woman, word_tfidf, tfidf_threshold)


In [25]:
def find_similar(word):
    similar_words = model.wv.most_similar(word, topn=5000)
    similar_words_filtered = filter_words_by_tfidf(similar_words, word_tfidf, tfidf_threshold)
    return similar_words, similar_words_filtered

In [26]:
print("\nFiltered similar words to 'γυναίκα':")
for word, score in similar_words_woman_filtered:
    print(word, score)


Filtered similar words to 'γυναίκα':
τότης 0.9996260404586792
καθώς 0.9996076226234436
γράφω 0.9995958805084229
όπλο 0.9995951652526855
τσι 0.9995841979980469
μόνος 0.9995818138122559
κορίτσι 0.999579906463623
γυναικόπαιδα 0.9995772242546082
παππός 0.9995735287666321
σχεδόν 0.9995690584182739
λυσίμαχος 0.9995675086975098
μάνα 0.9995602965354919
αντάρτης 0.9995598793029785
εαυτός 0.9995537996292114
φέρω 0.9995481371879578
καθένας 0.9995463490486145
δείχνω 0.9995449185371399
πορεία 0.9995430111885071
μεταξύ 0.999540388584137
αφήνω 0.9995403289794922
θάνατος 0.9995378255844116
πάντων 0.9995373487472534
αρχή 0.9995320439338684
πράγματι 0.9995284676551819
αφού 0.9995200037956238
κόσμος 0.9995194673538208
λληνη 0.9995164275169373
πάω 0.9995151162147522
σύντροφος 0.9995137453079224
χαρά 0.9995068311691284
οπλαρχηγός 0.9995050430297852
ιστορία 0.9995037317276001
τελικά 0.9995025396347046
φώναξε 0.9995008707046509
όνομα 0.9995003342628479
ρολόι 0.9994998574256897
πατρίδα 0.9994989037513733
φύγ

In [27]:
print("\nFiltered similar words to 'άνδρας':")
for word, score in similar_words_man:
    print(word, score)


Filtered similar words to 'άνδρας':
πέντε 0.9996445178985596
πέρασε 0.9995888471603394
δέκα 0.9995840191841125
δύο 0.9995790123939514
τέσσερις 0.9995744228363037
είκοσι 0.999538242816925
σειρά 0.9995317459106445
περίπου 0.9995279312133789
στρατιώτης 0.9995180368423462
κάρο 0.9995015263557434
μάχη 0.9994887709617615
πήρε 0.9994856119155884
φτάνω 0.9994778633117676
ρίχνω 0.999472975730896
τόσος 0.9994676113128662
ίσαμε 0.9994609355926514
βάρδιος 0.9994525909423828
βράδυ 0.9994474053382874
κοντά 0.9994429349899292
τριάντα 0.999441921710968
ομάδα 0.9994308948516846
ήρθε 0.9994054436683655
ερχόταν 0.9993978142738342
έξω 0.9993889331817627
άλλον 0.9993864893913269
αράδα 0.9993820190429688
οικογένεια 0.9993820190429688
μήνας 0.9993804097175598
πλήθος 0.9993802309036255
βήμα 0.9993789196014404
κιόλας 0.9993788003921509
σύντροφος 0.9993784427642822
σφαίρα 0.9993700385093689
περίμεναν 0.9993687272071838
πληθυσμός 0.9993630647659302
τόπος 0.999358057975769
άλογος 0.9993577599525452
νεκρός 0.9993

In [ ]:
print("\nFiltered similar words to 'άνδρας':")
for word, score in similar_words_man_filtered:
    print(word, score)

In [28]:
similar_words_black = model.wv.most_similar('μαύρος', topn=5000)
similar_words_black_filtered = filter_words_by_tfidf(similar_words_black, word_tfidf, tfidf_threshold)
for w in similar_words_black_filtered:
    print(w)

('παρακάτω', 0.9981287717819214)
('ιδιαίτερα', 0.9979928731918335)
('υπέρ', 0.9979461431503296)
('επιτροπή', 0.9979289174079895)
('ανθρώπινος', 0.9979256987571716)
('άγρια', 0.9979237914085388)
('μέχρι', 0.997921884059906)
('ρένος', 0.9979159235954285)
('γωνιά', 0.9979122877120972)
('αγίου', 0.9978988170623779)
('βρω', 0.9978980422019958)
('σιωπή', 0.9978963732719421)
('υπό', 0.9978826642036438)
('στόμα', 0.9978719353675842)
('πρόσωπος', 0.997871458530426)
('πλέον', 0.9978604912757874)
('άκουσα', 0.9978563189506531)
('δημοτικός', 0.9978544116020203)
('σταμάτης', 0.9978539347648621)
('χριστιανός', 0.9978499412536621)
('βομβαρδισμός', 0.9978455901145935)
('θάνατος', 0.9978414177894592)
('μέσω', 0.9978364706039429)
('μητροπολίτης', 0.9978359937667847)
('ανατολή', 0.9978237748146057)
('βάρος', 0.997822642326355)
('κεμάλ', 0.9978206157684326)
('προχωρώ', 0.9978176951408386)
('πρώτα', 0.9978148937225342)
('κόκκινος', 0.9978144764900208)
('ελληνικός', 0.9978119730949402)
('θανάτου', 0.9978117

In [29]:
print(corpus[4])

εκδοσεις ψυχογιος τατοου     μεταμορφωση αττικη τηλ               σησχημ σελ ράχη χαρτί παλατινα βιβλς ηλιοπουλοσροδοπουλοςς αληθινό αριστούργημα ιδιοφυα δύναμη φαντασία έξοχος τεχνικός αντώνη σαμαράκης δίνω ψυχολογικός πάλη ανάμεσα δύο πράκτος μυστικός υπηρεσία ασφάλεια ένας ολος κληρωτικός καθεστώς ύποπτος έχω καθεστώς είμαι τέλειος μηχανισμός εξόντωση ανθρώπου πλο πρά συλλαμβάνω ζούμε σήμερα σαν ηθοποιοί θέατρο κτορα ασφάλεια αμείλικτα τετράγωνη λογικός μου πλο επίσης παραλόγος ένας από λόγος τόσο επίμονη διάκριση μόνο ανάμεσα οπαδός εχθρός πολύ θαυμάζω λαθος είμαι γιατί έχω δύναμη αναλύω παράλογος μέσο ζούμε αίσθος πολίτης είμαι ύποπτος συνωμοσία ενάντια καθεστώς πρέπει βγει από χιούμορ ποίηση βάθος μέση αφού μόνος μάρτυρα κατηγορία υπεράσπιση είμαι δολοφονημένος αντωνης σαμαρακη αποφοίτησε από νομικός σχολή πανεπιστήμιο αθηνών δούλε από ίδιος πράκτορος τίθεται εφαρμογή σχέδιο πολίτης αντιμε πολύς χρόνος υπουργείο εργασία από όπου τωπίζω ένας δήθενς φιλικός ανθρώπινος συμπεριφορά σ

In [30]:
for w in all_tokens:
    print(w)

['ηλιο', 'βενεζη']
['ακαδημία', 'αθηνών']
['νούμερο']
['βιβλιο', 'σκλαβια']
['εισαγωγή', 'δημήτρης', 'δασκαλόπουλος']
['τεσσαρακοστος', 'εβδομος', 'εκδοση']
['βιβλιοπωλειον', 'εστια']
['κολλαρο', 'σιος']
['αθηνα']
['νούμερο', 'είμαι', 'ίδιος', 'ταυτότητα', 'συγγραφέα', 'παιδί']
['δεκαοκτώς', 'χρόνος', 'οδηγώ', 'από', 'τούρκους', 'σε ο', 'κάτεργα', 'ανατολή']
['βιβλίο', 'είμαι', 'ένας', 'συγκλονιστικός', 'χρονικός', 'γραμμένος', 'αίμα', 'όπως', 'επισημαίνω']
['βενέζης', 'προσθέτοντα', 'λέω', 'καυτής', 'ύλη', 'σάρκα', 'στάζω']
['αίμα', 'μου', 'πλημμυρίζω', 'σελίδα', 'αρχικός', 'μορφή', 'γράφτηκε']
['ξαναδουλεύτηκε', 'οπότε', 'εκδόθηκε', 'πρώτος', 'φορά', 'επιτυχία']
['σημείωσε', 'είμαι', 'τεράστιος', 'ακόμα', 'έξω', 'από', 'ελληνικός', 'χώρος']
['ηλία', 'βενέζης', 'βιβλίομαρτυρία', 'είμαι', 'γραώνμ', 'πρώτος', 'πρόσωπος']
['πραγματικός', 'όνομα', 'αφηγητήσυγγραφέα', 'γεννήθηκε', 'αϊβαλί', 'ρθε']
['Ελλάδα', 'μικρασιατικός', 'καταστροφή', 'θεωρώ', 'ένας', 'από']
['κυριότερους', 'εκπροσώπου

In [31]:
woman = set(similar_words_woman_filtered) - set(similar_words_man_filtered)
for c in woman:
    print(c)

('κυνηγός', 0.9994596838951111)
('περιγραφή', 0.9993019700050354)
('σκλάβος', 0.9992361664772034)
('θελε', 0.9991042613983154)
('φύγει', 0.9992870688438416)
('ήμουνα', 0.9994142055511475)
('έθνος', 0.9988601207733154)
('φωτιά', 0.9991509318351746)
('λοι', 0.9992949366569519)
('εντελώς', 0.9991084337234497)
('χαμηλός', 0.9988967180252075)
('κάναν', 0.9990738034248352)
('γαλήνη', 0.9988788962364197)
('πάμε', 0.9989127516746521)
('τέλειωσε', 0.9990841746330261)
('παλιός', 0.9993088245391846)
('ξαφνικά', 0.9994381666183472)
('λαός', 0.9994312524795532)
('δηλαδή', 0.999359667301178)
('ποτάμι', 0.9991747140884399)
('θανάτου', 0.999058187007904)
('γειτονιά', 0.999179482460022)
('αναφορά', 0.9990450739860535)
('ειδικός', 0.9989691376686096)
('αλή', 0.9990870356559753)
('θάνατος', 0.9995378255844116)
('ανθρώπου', 0.998967707157135)
('γίνανε', 0.999336838722229)
('κραυγή', 0.9989698529243469)
('είσαι', 0.9989156723022461)
('έπεσε', 0.9990723729133606)
('χρειάζομαι', 0.9991047978401184)
('αφέντη'

In [32]:
a = set(similar_words_man) - set(similar_words_man_filtered)
for c in a:
    print(c)

('κατάχαμα', 0.9985056519508362)
('Ελλάδα', 0.9987366795539856)


In [33]:
man = set(similar_words_man_filtered) - set(similar_words_woman_filtered)
for c in man:
    print(c)

('κείμενο', 0.9988320469856262)
('αρβύλος', 0.9986506104469299)
('σωρός', 0.9989645481109619)
('λυσίμαχος', 0.9987441301345825)
('εννέα', 0.9989676475524902)
('πασάς', 0.998779296875)
('χάρτης', 0.9987210631370544)
('αξιωματικός', 0.9989859461784363)
('μαύρα', 0.9989521503448486)
('μητροπολίτης', 0.9989097118377686)
('αϊτός', 0.9988481402397156)
('άρχισα', 0.9988771677017212)
('χατζή', 0.9985356330871582)
('σκοτωμένος', 0.9985073804855347)
('κυρίως', 0.999116063117981)
('βάλανς', 0.9985613822937012)
('σημειώνω', 0.9984893202781677)
('αθήνα', 0.9989287853240967)
('βάζω', 0.9989939332008362)
('μονομιάς', 0.9985765218734741)
('ψωμί', 0.999202311038971)
('δώσω', 0.9986710548400879)
('άφησε', 0.998932957649231)
('δείχνω', 0.9989602565765381)
('κατάφερε', 0.999118447303772)
('έφευγε', 0.99847811460495)
('περιοχή', 0.9992391467094421)
('έρχεται', 0.9990964531898499)
('δικαίωμα', 0.9988436698913574)
('τρόφιμα', 0.9990542531013489)
('άλογος', 0.9993577599525452)
('καταστροφή', 0.998843848705291

In [34]:
# Words to count
words_to_count = ['γυναίκα', 'άντρας']

# Count occurrences of each word in the corpus
word_counts = {word: sum([sentence.count(word) for sentence in all_tokens]) for word in words_to_count}

# Print the results
for word, count in word_counts.items():
    print(f"The word '{word}' appears {count} times in the corpus.")


The word 'γυναίκα' appears 302 times in the corpus.
The word 'άντρας' appears 222 times in the corpus.


In [35]:
# Words to count
words_to_count = ['κορίτσι', 'αγόρι']

# Count occurrences of each word in the corpus
word_counts = {word: sum([sentence.count(word) for sentence in all_tokens]) for word in words_to_count}

# Print the results
for word, count in word_counts.items():
    print(f"The word '{word}' appears {count} times in the corpus.")


The word 'κορίτσι' appears 109 times in the corpus.
The word 'αγόρι' appears 38 times in the corpus.


In [36]:
girl, girl_filtered = find_similar('κορίτσι')
for c in girl_filtered:
    print(c)

('λυσίμαχος', 0.9997135400772095)
('πράγματι', 0.9997045397758484)
('αποφασίζω', 0.99969881772995)
('σχεδόν', 0.9996970891952515)
('προσπαθώ', 0.9996939301490784)
('τελικά', 0.9996911287307739)
('πασάς', 0.9996804594993591)
('ωστόσο', 0.9996798038482666)
('μεταξύ', 0.9996756315231323)
('ψυχή', 0.9996728897094727)
('έστω', 0.9996716976165771)
('καθώς', 0.9996707439422607)
('όπλο', 0.9996632933616638)
('οπλαρχηγός', 0.9996619820594788)
('φύγω', 0.9996590614318848)
('μόνος', 0.9996589422225952)
('ταξίδι', 0.9996578693389893)
('λέξη', 0.9996573328971863)
('αλέκος', 0.999656081199646)
('αφού', 0.9996549487113953)
('αρχή', 0.9996540546417236)
('πάντα', 0.9996529817581177)
('γράφω', 0.9996516704559326)
('μάλλον', 0.9996492266654968)
('έμενε', 0.9996451735496521)
('σκοπός', 0.9996436238288879)
('διότι', 0.9996431469917297)
('ιστορία', 0.999642550945282)
('διαταγή', 0.9996423721313477)
('μοίρα', 0.9996420741081238)
('συνεπώς', 0.9996408224105835)
('περιμένω', 0.999640166759491)
('έργο', 0.99963